In [19]:

import librosa
import numpy as np
import pandas as pd
from keras.layers import Dense
from keras.models import Sequential
from pydub import AudioSegment
from scipy import signal
from sklearn import preprocessing

In [20]:
pathAudio = 'C:/Users/Admin/OneDrive/Dokumente/Studium/Technology Lab/Technology Lab Team 4/Techno Titel/train-stochastic/samples/'
files = librosa.util.find_files(pathAudio, ext=['mp3'])
files = sorted(files, key=lambda x: int(x.split('_')[-1].split(".")[0]))

In [21]:
def normalize_sample(sample):
    array_of_samples = sample.get_array_of_samples()
    np_arr = np.array(array_of_samples)
    np_arr = np_arr.reshape(1, -1)
    return preprocessing.normalize(np_arr)


samples = []
samples_sec_canal = []
for file_name in files:
    sample = AudioSegment.from_mp3(file_name)
    mono_samples = sample.split_to_mono()
    normalized_sample = normalize_sample(mono_samples[0])[0]
    resampled_sample = signal.resample(normalized_sample, 1000)
    samples.append(resampled_sample)
    normalized_sample_sec_canal = normalize_sample(mono_samples[1])[0]
    resampled_sample_sec_canal = signal.resample(normalized_sample_sec_canal, 1000)
    samples_sec_canal.append(resampled_sample_sec_canal)

In [22]:
X_train = []
Y_train = []
for i in range(len(samples)):
    Y_train.append(i)
    if i < len(samples) - 1:
        x = list(samples[i])
        y = list(samples[i + 1])
        z = x + y
        X_train.append(z)
    else:
        x = list(samples[i])
        y = list(samples[0])
        z = x + y
        X_train.append(z)

In [23]:
from numpy import random

X_train_false = []


def get_strange_end_part(samples, current_index, max_len):
    x = random.randint(max_len)
    if x != current_index:
        return samples[x]
    else:
        return get_strange_end_part(samples, current_index, max_len)


for i in range(len(samples)):
    first_half = samples[i]
    last_half = get_strange_end_part(samples, i, len(samples))
    new_sample = list(first_half) + list(last_half)
    X_train_false.append(new_sample)

In [24]:
X_train = np.array(X_train)
X_train = X_train.reshape(-1, 2000)

In [25]:
from keras.utils.np_utils import to_categorical

Y_train = to_categorical(Y_train)

In [26]:
Y_train = np.array(Y_train)
Y_train.shape

(126, 126)

In [27]:
X_train = X_train.reshape(-1, 2000)
X_train.shape

(126, 2000)

In [16]:
from keras.layers import Conv1D, LSTM, Flatten

model = Sequential()
model.add(Conv1D(filters=10, kernel_size=1, input_shape=(2000, 1)))
model.add(LSTM(20, return_sequences=True))
model.add(Dense(100))
model.add(Flatten())
model.add(Dense(151, activation='sigmoid'))

model.compile(optimizer='rmsprop', loss='categorical_crossentropy', metrics=['accuracy'])
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d (Conv1D)             (None, 2000, 10)          20        
                                                                 
 lstm (LSTM)                 (None, 2000, 20)          2480      
                                                                 
 dense (Dense)               (None, 2000, 100)         2100      
                                                                 
 flatten (Flatten)           (None, 200000)            0         
                                                                 
 dense_1 (Dense)             (None, 243)               48600243  
                                                                 
Total params: 48,604,843
Trainable params: 48,604,843
Non-trainable params: 0
_________________________________________________________________


In [17]:
model.fit(X_train, Y_train, epochs=50)

Epoch 1/50
4/4 [==============================] - 5s 724ms/step - loss: 6.2556 - accuracy: 0.0000e+00
Epoch 2/50
4/4 [==============================] - 3s 732ms/step - loss: 5.8311 - accuracy: 0.0082
Epoch 3/50
4/4 [==============================] - 3s 719ms/step - loss: 5.6131 - accuracy: 0.0123
Epoch 4/50
4/4 [==============================] - 3s 723ms/step - loss: 5.4839 - accuracy: 0.0041
Epoch 5/50
4/4 [==============================] - 3s 716ms/step - loss: 5.5388 - accuracy: 0.0041
Epoch 6/50
4/4 [==============================] - 3s 726ms/step - loss: 5.5187 - accuracy: 0.0000e+00
Epoch 7/50
4/4 [==============================] - 3s 720ms/step - loss: 5.4855 - accuracy: 0.0082
Epoch 8/50
4/4 [==============================] - 3s 719ms/step - loss: 5.5602 - accuracy: 0.0165
Epoch 9/50
4/4 [==============================] - 3s 716ms/step - loss: 5.4696 - accuracy: 0.0206
Epoch 10/50
4/4 [==============================] - 3s 715ms/step - loss: 5.4842 - accuracy: 0.0082
Epoch 11/50

In [18]:
x_val = []
for i in range(len(samples_sec_canal)):
    if i < len(samples_sec_canal) - 1:
        x = list(samples_sec_canal[i])
        y = list(samples_sec_canal[i + 1])
        z = x + y
        x_val.append(z)
    else:
        x = list(samples_sec_canal[i])
        y = list(samples_sec_canal[0])
        z = x + y
        x_val.append(z)
x_val = np.array(x_val)
pred = model.predict(x_val)
y_pred = pd.Series(np.argmax(pred, axis=1), name='pred')
y_pred

0        0
1       44
2        2
3        3
4        4
      ... 
238    194
239    114
240     90
241     44
242    242
Name: pred, Length: 243, dtype: int64

In [110]:
from pathlib import Path

path_all_samples = 'C:/Users/Admin/OneDrive/Dokumente/Studium/Technology Lab/Technology Lab Team 4/Techno Titel/music-pool/samples/all_samples'
sample_files = librosa.util.find_files(path_all_samples, ext=['mp3'])
sample_files = sample_files
loaded_samples = {}
for file_path in sample_files:
    loaded_audio_file = AudioSegment.from_mp3(file_path)
    sample_array = loaded_audio_file.get_array_of_samples()
    resampled_part = signal.resample(sample_array, 1000)
    file_name = Path(file_path).stem
    loaded_samples[file_name] = resampled_part

In [125]:
i = 0
current_class = 0
reference_sample = samples[0]
max = 151
selected_samples = ['Tea K Pea - nauticals_1']
while i < max:
    best_sample_name = None
    best_score = 0.00000
    best_sample = []
    for key, value in loaded_samples.items():
        if key not in selected_samples:
            ref_and_sample = np.append(reference_sample, value)
            prediction = model.predict(ref_and_sample.reshape(1, 2000))
            score = prediction[0][current_class]
            if score > best_score:
                best_score = score
                best_sample_name = key
                best_sample = value
            if score > 0.95:
                break
    print('Predicted ' + best_sample_name + ' at class ' + str(current_class) + ' as best sample with score ' + str(
        best_score))
    reference_sample = best_sample
    selected_samples.append(best_sample_name)
    i += 1
    current_class += 1

Predicted Brylie Christopher Oxley - City view from Torni_128 at class 0 as best sample with score 0.99999976
Predicted Maarten Schellekens - Lounge It_28 at class 1 as best sample with score 3.9959865e-05
Predicted Baners - Use It_2 at class 2 as best sample with score 1.0
Predicted Brylie Christopher Oxley - City view from Torni_107 at class 3 as best sample with score 1.0
Predicted Baners - Use It_3 at class 4 as best sample with score 1.0
Predicted Brylie Christopher Oxley - City view from Torni_127 at class 5 as best sample with score 1.0
Predicted Baners - Use It_4 at class 6 as best sample with score 1.0
Predicted Tea K Pea - nauticals_87 at class 7 as best sample with score 3.8711593e-07
Predicted Baners - Use It_5 at class 8 as best sample with score 1.0
Predicted Baners - Use It_6 at class 9 as best sample with score 0.9829258
Predicted Baners - Use It_7 at class 10 as best sample with score 1.0
Predicted Blue Sky Moon- Smallest Things In The Forest_1 at class 11 as best samp

In [126]:
new_song = AudioSegment.empty()
for sample in selected_samples:
    complete_path = 'C:/Users/Admin/OneDrive/Dokumente/Studium/Technology Lab/Technology Lab Team 4/Techno Titel/music-pool/samples/all_samples/' + sample + '.mp3'
    loaded_sample = AudioSegment.from_mp3(complete_path)
    new_song += loaded_sample
new_song.export('C:/Users/Admin/OneDrive/Dokumente/Studium/Technology Lab/Technology Lab Team 4/Techno Titel/music_out/' + 'karacho_c3.mp3', format='mp3')

<_io.BufferedRandom name='C:/Users/Admin/OneDrive/Dokumente/Studium/Technology Lab/Technology Lab Team 4/Techno Titel/music_out/karacho_c3.mp3'>

In [127]:
new_song